# For certain metrics, aggregate them to quarterly in `merge_data`

* Tiffany's Teams message: 
 > you can do it within merge_data for now, it'll be the quickest way to get your quarterly averages. 
merge_data is simply concatenating schedule, summary speeds, rt vs schedule by route-direction-peak/offpeak-single day together. You can take that and aggregate several days into quarterly.
Here's the script for average_segment_speeds that mocks up aggregating across single days / using weighted averages, and you'll see how some of the functions are put together, specifically tagging the quarter-year / weekday or weekend / weighted averages (using n_trips) to weight the metric column. https://github.com/cal-itp/data-analyses/blob/main/rt_segment_speeds/scripts/average_segment_speeds.py
* Metrics to Roll Up
    * Avg scheduled minute
    * VP per minute
    * Spatial Accuracy

In [1]:
import _report_utils
import _section1_utils as section1
import _section2_utils as section2
import geopandas as gpd
import merge_data
import numpy as np
import pandas as pd
from segment_speed_utils import gtfs_schedule_wrangling, helpers, segment_calcs
from segment_speed_utils.project_vars import COMPILED_CACHED_VIEWS, PROJECT_CRS
from shared_utils import (
    catalog_utils,
    portfolio_utils,
    rt_dates,
    rt_utils,
    time_helpers,
)
from update_vars import GTFS_DATA_DICT, RT_SCHED_GCS, SCHED_GCS, SEGMENT_GCS

# Data Dictionary
GTFS_DATA_DICT = catalog_utils.get_catalog("gtfs_analytics_data")

In [2]:
pd.options.display.max_columns = 100
pd.options.display.float_format = "{:.2f}".format
pd.set_option("display.max_rows", None)
pd.set_option("display.max_colwidth", None)

In [3]:
analysis_date_list = [rt_dates.DATES["feb2025"]]

In [4]:
analysis_date = rt_dates.DATES["feb2025"]

In [5]:
schd_vp_url = f"{GTFS_DATA_DICT.digest_tables.dir}{GTFS_DATA_DICT.digest_tables.route_schedule_vp}.parquet"

In [6]:
sdi = "San Diego Metropolitan Transit System"

In [7]:
df = section2.load_schedule_vp_metrics(sdi)

In [8]:
df.columns

Index(['schedule_gtfs_dataset_key', 'dir_0_1', 'Period',
       'Average Scheduled Service (trip minutes)',
       'Average Stop Distance (miles)', '# scheduled trips', 'Trips per Hour',
       'is_express', 'is_rapid', 'is_rail', 'is_coverage', 'is_downtown_local',
       'is_local', 'Date', 'Route typology', '# Minutes with 1+ VP per Minute',
       '# Minutes with 2+ VP per Minute', 'Aggregate Actual Service Minutes',
       'Aggregate Scheduled Service Minutes (all trips)', '# VP',
       '# VP within Scheduled Shape', '# Early Arrival Trips',
       '# On-Time Trips', '# Late Trips', '# Trips with VP',
       'Average VP per Minute', '% VP within Scheduled Shape',
       'pct_rt_journey_atleast1_vp', 'pct_rt_journey_atleast2_vp',
       '% Scheduled Trip w/ 1+ VP/Minute', '% Scheduled Trip w/ 2+ VP/Minute',
       'Realtime versus Scheduled Service Ratio',
       'Average Actual Service (Trip Minutes)', 'GTFS Availability',
       'Speed (MPH)', 'route_long_name', 'route_short_nam

## Subset df

In [9]:
# Filter out to all day
all_day = df.loc[df.Period == "all_day"].reset_index(drop=True)

In [10]:
all_day.sample()

schedule_gtfs_dataset_key  dir_0_1   Period  \
3462  baeeb157e85a901e47b828ef9fe75091     1.00  all_day   

      Average Scheduled Service (trip minutes)  Average Stop Distance (miles)  \
3462                                     18.14                           0.35   

      # scheduled trips  Trips per Hour  is_express  is_rapid  is_rail  \
3462                 85            3.54        0.00      0.00     0.00   

      is_coverage  is_downtown_local  is_local       Date Route typology  \
3462         1.00               0.00      0.00 2023-12-13       coverage   

      # Minutes with 1+ VP per Minute  # Minutes with 2+ VP per Minute  \
3462                             2439                             2119   

      Aggregate Actual Service Minutes  \
3462                           2423.39   

      Aggregate Scheduled Service Minutes (all trips)  # VP  \
3462                                          1542.00  5278   

      # VP within Scheduled Shape  # Early Arrival Trips  # On-Time Trips  \
3462                         4869                      0               14   

      # Late Trips  # Trips with VP  Average VP per Minute  \
3462            71               85                   2.18   

      % VP within Scheduled Shape  pct_rt_journey_atleast1_vp  \
3462                        92.00                      100.00   

      pct_rt_journey_atleast2_vp  % Scheduled Trip w/ 1+ VP/Minute  \
3462                       87.00                            100.00   

      % Scheduled Trip w/ 2+ VP/Minute  \
3462                            100.00   

      Realtime versus Scheduled Service Ratio  \
3462                                     1.57   

      Average Actual Service (Trip Minutes) GTFS Availability  Speed (MPH)  \
3462                                  28.51   schedule_and_vp        15.78   

                                     route_long_name route_short_name  \
3462  Iris Transit Center - Otay Mesa Transit Center              905   

                                                   Route Route ID  \
3462  905 Iris Transit Center - Otay Mesa Transit Center      905   

                                                                   Base64 Encoded Feed URL  \
3462  aHR0cHM6Ly93d3cuc2RtdHMuY29tL2dvb2dsZV90cmFuc2l0X2ZpbGVzL2dvb2dsZV90cmFuc2l0LnppcA==   

        Organization ID                           Organization  \
3462  recZALk4vysuoTVjF  San Diego Metropolitan Transit System   

            District  Direction    Transit Operator schedule_source_record_id  \
3462  11 - San Diego  Westbound  San Diego Schedule         recfZ9iWkptccoONX   

      ruler_100_pct  ruler_for_vp_per_min  headway_in_minutes quarter  
3462            100                     2               16.95  2023Q4

### The results are really off for `Average VP per Minute`

In [11]:
def quarterly_rollup(all_day: pd.DataFrame) -> pd.DataFrame:
    """
    Using the dataframe that houses only all_day values,
    roll up months to each quarter for certain metrics.
    """
    # Turn date to quarters
    all_day["quarter"] = pd.PeriodIndex(all_day.Date, freq="Q").astype("str")

    quarterly_metrics = segment_calcs.calculate_weighted_averages(
        df=all_day,
        group_cols=[
            "quarter",
            "Organization",
            "Route",
            "dir_0_1",
            "Direction",
        ],
        metric_cols=[
            "Average VP per Minute",
            "% VP within Scheduled Shape",
            "Average Scheduled Service (trip minutes)",
            "ruler_100_pct",
            "ruler_for_vp_per_min",
        ],
        weight_col="# Trips with VP",
    )
    return quarterly_metrics

In [12]:
all_metrics_test = quarterly_rollup(all_day)

## Test charts

In [13]:
import yaml

with open("readable.yml") as f:
    readable_dict = yaml.safe_load(f)

In [14]:
# Color Palette
with open("color_palettes.yml") as f:
    color_dict = yaml.safe_load(f)

In [15]:
all_metrics_test.sample(3)

quarter                           Organization  \
447   2023Q3  San Diego Metropolitan Transit System   
542   2023Q3  San Diego Metropolitan Transit System   
1222  2024Q3  San Diego Metropolitan Transit System   

                                                 Route  dir_0_1   Direction  \
447   709 H St Transit Center - Otay Ranch Town Center     1.00   Westbound   
542           968 8th St Transit Center - Plaza Bonita     1.00   Westbound   
1222        872 El Cajon Shuttle Loop Counterclockwise     1.00  Northbound   

      Average VP per Minute  % VP within Scheduled Shape  \
447                    1.53                        95.67   
542                    1.52                        95.33   
1222                   2.20                        98.31   

      Average Scheduled Service (trip minutes)  ruler_100_pct  \
447                                      39.08         100.00   
542                                      24.19         100.00   
1222                                     19.54         100.00   

      ruler_for_vp_per_min  # Trips with VP  
447                   2.00              180  
542                   2.00               48  
1222                  2.00               72

In [16]:
all_metrics_test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1645 entries, 0 to 1644
Data columns (total 11 columns):
 #   Column                                    Non-Null Count  Dtype  
---  ------                                    --------------  -----  
 0   quarter                                   1645 non-null   object 
 1   Organization                              1645 non-null   object 
 2   Route                                     1645 non-null   object 
 3   dir_0_1                                   1645 non-null   float64
 4   Direction                                 1645 non-null   object 
 5   Average VP per Minute                     1645 non-null   float64
 6   % VP within Scheduled Shape               1645 non-null   float64
 7   Average Scheduled Service (trip minutes)  1645 non-null   float64
 8   ruler_100_pct                             1645 non-null   float64
 9   ruler_for_vp_per_min                      1645 non-null   float64
 10  # Trips with VP                     

In [17]:
# Charts
import altair as alt

alt.data_transformers.enable("default", max_rows=None)

DataTransformerRegistry.enable('default')

In [18]:
def grouped_bar_chart(
    df: pd.DataFrame,
    color_col: str,
    y_col: str,
    offset_col: str,
    title: str,
    subtitle: str,
    range_color: list,
    quarter: bool = False,
) -> alt.Chart:

    tooltip_cols = [
        "Route",
        "Direction",
        color_col,
        y_col,
    ]

    if quarter == False:
        # Clean dataframe
        tooltip_cols.append("Period")
        tooltip_cols.append("Date")
        df = clean_data_charts(df, y_col)

        chart = (
            alt.Chart(df)
            .mark_bar(size=5)
            .encode(
                x=alt.X(
                    "yearmonthdate(Date):O",
                    title=["Date"],
                    axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                ),
                y=alt.Y(f"{y_col}:Q", title=_report_utils.labeling(y_col)),
                xOffset=alt.X(
                    f"{offset_col}:N", title=_report_utils.labeling(offset_col)
                ),
                color=alt.Color(
                    f"{color_col}:N",
                    title=_report_utils.labeling(color_col),
                    scale=alt.Scale(range=range_color),
                ),
                tooltip=tooltip_cols,
            )
        )
    else:
        tooltip_cols.append("quarter")
        chart = (
            alt.Chart(df)
            .mark_bar(size=5)
            .encode(
                x=alt.X(
                    "quarter",
                    title=["Quarter"],
                    axis=alt.Axis(labelAngle=-45),
                ),
                y=alt.Y(f"{y_col}:Q", title=_report_utils.labeling(y_col)),
                xOffset=alt.X(
                    f"{offset_col}:N", title=_report_utils.labeling(offset_col)
                ),
                color=alt.Color(
                    f"{color_col}:N",
                    title=_report_utils.labeling(color_col),
                    scale=alt.Scale(range=range_color),
                ),
                tooltip=tooltip_cols,
            )
        )

    chart = (chart).properties(
        title={
            "text": title,
            "subtitle": [subtitle],
        },
        width=400,
        height=250,
    )

    return chart

In [19]:
all_metrics_test.columns

Index(['quarter', 'Organization', 'Route', 'dir_0_1', 'Direction',
       'Average VP per Minute', '% VP within Scheduled Shape',
       'Average Scheduled Service (trip minutes)', 'ruler_100_pct',
       'ruler_for_vp_per_min', '# Trips with VP'],
      dtype='object')

In [20]:
# Create dropdown
routes_list = all_metrics_test["Route"].unique().tolist()

route_dropdown = alt.binding_select(
    options=routes_list,
    name="Routes: ",
)
# Column that controls the bar charts
xcol_param = alt.selection_point(
    fields=["Route"], value=routes_list[0], bind=route_dropdown
)

### Average Scheduled Service (trip minutes)

In [21]:
(
    grouped_bar_chart(
        df=all_metrics_test,
        color_col="Direction",
        y_col="Average Scheduled Service (trip minutes)",
        offset_col="Direction",
        title=readable_dict["avg_scheduled_min_graph"]["title"],
        subtitle=readable_dict["avg_scheduled_min_graph"]["subtitle"],
        range_color=color_dict["four_colors"],
        quarter=True,
    )
).add_params(xcol_param).transform_filter(xcol_param)

alt.Chart(...)

### % VP within Scheduled Shape

In [22]:
def base_facet_with_ruler_chart(
    df: pd.DataFrame,
    y_col: str,
    ruler_col: str,
    title: str,
    subtitle: str,
    domain_color: list,
    range_color: list,
    quarter: bool = False,
) -> alt.Chart:

    tooltip_cols = [
        "Route",
        "Direction",
        y_col,
    ]

    # Set y-axis
    max_y = section2.set_y_axis(df, y_col)

    # Clean dataframe
    df = section2.clean_data_charts(df, y_col)

    # Create color scale
    color_scale = alt.Scale(domain=domain_color, range=range_color)

    # Create ruler
    ruler = (
        alt.Chart(df)
        .mark_rule(color="red", strokeDash=[10, 7])
        .encode(y=f"mean({ruler_col}):Q")
    )
    if quarter == False:
        tooltip_cols.append("Period")
        tooltip_cols.append("Date")
        chart = (
            alt.Chart(df)
            .mark_bar(size=7, clip=True)
            .encode(
                x=alt.X(
                    "yearmonthdate(Date):O",
                    title=[x_col],
                    axis=alt.Axis(labelAngle=-45, format="%b %Y"),
                ),
                y=alt.Y(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=alt.Scale(domain=[0, max_y]),
                ),
                color=alt.Color(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=color_scale,
                ),
                tooltip=df[tooltip_cols].columns.tolist(),
            )
        )
    else:
        tooltip_cols.append("quarter")
        chart = (
            alt.Chart(df)
            .mark_bar(size=7, clip=True)
            .encode(
                x=alt.X(
                    "quarter",
                    title="Quarter",
                    axis=alt.Axis(labelAngle=-45),
                ),
                y=alt.Y(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=alt.Scale(domain=[0, max_y]),
                ),
                color=alt.Color(
                    f"{y_col}:Q",
                    title=_report_utils.labeling(y_col),
                    scale=color_scale,
                ),
                tooltip=df[tooltip_cols].columns.tolist(),
            )
        )
    # All charts
    chart = (chart + ruler).properties(width=200, height=250)
    chart = chart.facet(
        column=alt.Column(
            "Direction:N",
        )
    ).properties(
        title={
            "text": title,
            "subtitle": [subtitle],
        }
    )

    return chart

In [23]:
color_dict["spatial_accuracy_range"]

['#dd217d', '#fc5c04', '#ff9c42', '#fcb40e', '#e9d868', '#ccbb44']

In [24]:
base_facet_with_ruler_chart(
    df=all_metrics_test,
    y_col="% VP within Scheduled Shape",
    ruler_col="ruler_100_pct",
    title=readable_dict["spatial_accuracy_graph"]["title"],
    subtitle=readable_dict["spatial_accuracy_graph"]["subtitle"],
    domain_color=color_dict["spatial_accuracy_domain"],
    range_color=color_dict["spatial_accuracy_range"],
    quarter=True,
).add_params(xcol_param).transform_filter(xcol_param)

alt.FacetChart(...)

### Average VP per Minute

In [25]:
(
    (
        base_facet_with_ruler_chart(
            all_metrics_test,
            "Average VP per Minute",
            "ruler_for_vp_per_min",
            readable_dict["vp_per_min_graph"]["title"],
            readable_dict["vp_per_min_graph"]["subtitle"],
            color_dict["vp_domain"],
            color_dict["vp_range"],
            quarter=True,
        )
    )
    .add_params(xcol_param)
    .transform_filter(xcol_param)
)

alt.FacetChart(...)

In [26]:
all_metrics_test.loc[
    (all_metrics_test.Organization == "San Diego Metropolitan Transit System")
    & (all_metrics_test["Route"] == "1 Fashion Valley - La Mesa")
    & (all_metrics_test.quarter == "2023Q3")
]

quarter                           Organization  \
368  2023Q3  San Diego Metropolitan Transit System   
369  2023Q3  San Diego Metropolitan Transit System   

                          Route  dir_0_1  Direction  Average VP per Minute  \
368  1 Fashion Valley - La Mesa     0.00  Eastbound                      1   
369  1 Fashion Valley - La Mesa     1.00  Westbound                      1   

     % VP within Scheduled Shape  Average Scheduled Service (trip minutes)  \
368                           97                                     62.04   
369                           94                                     57.56   

     ruler_100_pct  ruler_for_vp_per_min  # Trips with VP  \
368         100.00                  2.00              150   
369         100.00                  2.00              156   

    % VP within Scheduled Shape_str Average VP per Minute_str  
368                              97                         1  
369                              94                         1

### % of Scheduled Trip Journey chart is messed up due to the rulers

In [27]:
df.head(1)

schedule_gtfs_dataset_key  dir_0_1   Period  \
0  1adf7a7bde86b42ed014f6de74c7132e     0.00  all_day   

   Average Scheduled Service (trip minutes)  Average Stop Distance (miles)  \
0                                     62.04                           0.17   

   # scheduled trips  Trips per Hour  is_express  is_rapid  is_rail  \
0                 50            2.08        0.00      1.00     0.00   

   is_coverage  is_downtown_local  is_local       Date Route typology  \
0         0.00               1.00      0.00 2023-04-12          rapid   

   # Minutes with 1+ VP per Minute  # Minutes with 2+ VP per Minute  \
0                             3292                             2373   

   Aggregate Actual Service Minutes  \
0                           4651.70   

   Aggregate Scheduled Service Minutes (all trips)  # VP  \
0                                          3102.00  5907   

   # VP within Scheduled Shape  # Early Arrival Trips  # On-Time Trips  \
0                         5818                      2               31   

   # Late Trips  # Trips with VP  Average VP per Minute  \
0            17               50                   1.27   

   % VP within Scheduled Shape  pct_rt_journey_atleast1_vp  \
0                        98.00                       71.00   

   pct_rt_journey_atleast2_vp  % Scheduled Trip w/ 1+ VP/Minute  \
0                       51.00                            100.00   

   % Scheduled Trip w/ 2+ VP/Minute  Realtime versus Scheduled Service Ratio  \
0                             76.00                                     1.50   

   Average Actual Service (Trip Minutes) GTFS Availability  Speed (MPH)  \
0                                  93.03   schedule_and_vp        11.10   

            route_long_name route_short_name                       Route  \
0  Fashion Valley - La Mesa                1  1 Fashion Valley - La Mesa   

  Route ID  \
0        1   

                                                                Base64 Encoded Feed URL  \
0  aHR0cHM6Ly93d3cuc2RtdHMuY29tL2dvb2dsZV90cmFuc2l0X2ZpbGVzL2dvb2dsZV90cmFuc2l0LnppcA==   

     Organization ID                           Organization        District  \
0  recZALk4vysuoTVjF  San Diego Metropolitan Transit System  11 - San Diego   

   Direction    Transit Operator schedule_source_record_id  ruler_100_pct  \
0  Eastbound  San Diego Schedule         recfZ9iWkptccoONX            100   

   ruler_for_vp_per_min  headway_in_minutes quarter  
0                     2               28.85  2023Q2

In [28]:
sched_journey_vp = section2.pct_vp_journey(
    all_day,
    "% Scheduled Trip w/ 1+ VP/Minute",
    "% Scheduled Trip w/ 2+ VP/Minute",
)

In [29]:
sched_journey_vp.shape

(8568, 8)

In [30]:
sched_journey_vp.ruler_100_pct.describe()

count   8568.00
mean     100.00
std        0.00
min      100.00
25%      100.00
50%      100.00
75%      100.00
max      100.00
Name: ruler_100_pct, dtype: float64

In [31]:
sched_journey_vp.head(1)

Date                           Organization  \
0 2023-04-12  San Diego Metropolitan Transit System   

                        Route  Direction   Period  \
0  1 Fashion Valley - La Mesa  Eastbound  all_day   

                           Category  % of Actual Trip Minutes  ruler_100_pct  
0  % Scheduled Trip w/ 1+ VP/Minute                    100.00            100

In [32]:
(
    section2.base_facet_circle(
        sched_journey_vp,
        "% of Actual Trip Minutes",
        "Category",
        "ruler_100_pct",
        readable_dict["sched_vp_per_min_graph"]["title"],
        readable_dict["sched_vp_per_min_graph"]["subtitle"],
        color_dict["tri_color"],
    )
    .add_params(xcol_param)
    .transform_filter(xcol_param)
)

alt.FacetChart(...)

### Change Total Scheduled Trips -> the graph is cutting off in a strange fashion.

In [33]:
peak_offpeak_df = df.loc[df["Period"] != "all_day"].reset_index(drop=True)

In [34]:
def rollup_schd_qtr(peak_offpeak_df:pd.DataFrame)->pd.DataFrame:
    """
    Roll up # Scheduled Trips to be on a quarterly basis
    since this metric doesn't change very often. 
    """
    # Aggregate
    agg1 = (
    peak_offpeak_df.groupby(
        ["quarter", "Period", "Organization", "Route", "dir_0_1", "Direction"]
    )
    .agg({"Date":"nunique","# scheduled trips": "sum"})
    .reset_index()
    )
    
    # If a quarter is complete with all 3 months, divide by 3
    agg1.loc[agg1["Date"] == 3, "# scheduled trips"] = (
    agg1.loc[agg1["Date"] == 3, "# scheduled trips"] / 3)
    
    # If a quarter is incomplete with only 2 months, divide by 2 
    agg1.loc[agg1["Date"] == 2, "# scheduled trips"] = (
    agg1.loc[agg1["Date"] == 2, "# scheduled trips"] / 2
)
    return agg1

In [35]:
total_scheduled_trips = rollup_schd_qtr(peak_offpeak_df)

In [36]:
(
    section2.grouped_bar_chart(
        total_scheduled_trips.loc[(total_scheduled_trips.dir_0_1 == 0)],
        color_col="Period",
        y_col="# scheduled trips",
        offset_col="Period",
        title=readable_dict["trips_per_day_graph"]["title"],
        subtitle="",
        range_color=color_dict["spatial_accuracy_range"],
        quarter=True,
    )
    .add_params(xcol_param)
    .transform_filter(xcol_param)
)

alt.Chart(...)

In [37]:
total_scheduled_trips.head(1)

quarter   Period                           Organization  \
0  2023Q1  offpeak  San Diego Metropolitan Transit System   

                        Route  dir_0_1  Direction  Date  # scheduled trips  
0  1 Fashion Valley - La Mesa     0.00  Eastbound     1              27.00

In [49]:
def stacked_bar_chart(
    df: pd.DataFrame,
    y_col: str,
    color_col: str,
    title: str,
    subtitle: str,
    range_color:list,
    quarter: bool = False
)-> alt.Chart:
    tooltip_cols = [
        "Route",
        "Direction",
        y_col,
    ]
    
    # Set y-axis
    max_y = section2.set_y_axis(df, y_col)
    
    # Clean dataframe
    df = section2.clean_data_charts(df, y_col)

    if quarter == False:
        tooltip_cols.append("Period")
        tooltip_cols.append("Date")
        chart = (
        alt.Chart(df)
        .mark_bar(size=7, clip=True)
        .encode(
            x=alt.X(
                "yearmonthdate(Date):O",
                title=["Date"],
                axis=alt.Axis(labelAngle=-45, format="%b %Y"),
            ),
            y=alt.Y(
                f"{y_col}:Q",
                title=_report_utils.labeling(y_col),
                scale=alt.Scale(domain=[0, max_y]),
            ),
            color=alt.Color(
                f"{color_col}:N",
                title=_report_utils.labeling(color_col),
                scale=alt.Scale(range=color_dict["four_colors"]),
            ),
            tooltip=tooltip_cols,
        )
    )
    
    else:
        tooltip_cols.append("quarter")
        chart = (
        alt.Chart(df)
        .mark_bar(size=7, clip=True)
        .encode(
            x=alt.X(
                "quarter",
                title=["Quarter"],
                axis=alt.Axis(labelAngle=-45),
            ),
            y=alt.Y(
                f"{y_col}:Q",
                title=_report_utils.labeling(y_col),
                scale=alt.Scale(domain=[0, max_y]),
            ),
            color=alt.Color(
                f"{color_col}:N",
                title=_report_utils.labeling(color_col),
                scale=alt.Scale(range=color_dict["four_colors"]),
            ),
            tooltip=tooltip_cols,
        )
    )
        
    chart = chart.properties(width=200, height=250)
    
    # Facet the chart
    chart = chart.properties(
        title={
            "text": title,
            "subtitle": subtitle,
        }
    )

    return chart

In [51]:
stacked_bar_chart(
df = total_scheduled_trips.loc[total_scheduled_trips.dir_0_1 == 0],
y_col = "# scheduled trips",
color_col = "Period",
title = "",
subtitle = "",
range_color=color_dict["four_colors"],
quarter = True).add_params(xcol_param).transform_filter(xcol_param)

alt.Chart(...)

In [46]:
(
        alt.Chart(total_scheduled_trips.loc[total_scheduled_trips.dir_0_1 == 0])
        .mark_bar(size=7, clip=True)
        .encode(
            x=alt.X(
                "quarter",
                title=["quarter"],
                axis=alt.Axis(labelAngle=-45),
            ),
            y=alt.Y(
                "# scheduled trips:Q",
                title=_report_utils.labeling("# scheduled trips",),
                scale=alt.Scale(domain=[0, 100]),
            ),
            color=alt.Color(
                "Period:N",
                title=_report_utils.labeling("Period"),
                scale=alt.Scale(range=color_dict["four_colors"]),
            ),
            tooltip=list(total_scheduled_trips.columns),
        )
    ).add_params(xcol_param).transform_filter(xcol_param)

alt.Chart(...)

In [38]:
(
            (
                section2.base_facet_chart(
                    df = total_scheduled_trips,
                    direction_to_filter = 0,
                    y_col = "# scheduled trips",
                    color_col = "Period",
                    facet_col = "Period",
                    title = readable_dict["trips_per_day_graph"]["title"],
                    subtitle = "",
                    range_color = color_dict["four_colors"]
                )
            )
            .add_params(xcol_param)
            .transform_filter(xcol_param)
        )

alt.FacetChart(...)

In [ ]:
# Peak East bound
23 + 23 + 23

## Turn off group keys for the `segment_calcs.calculate_weighted_averages` function
* This didn't work at all. 

In [ ]:
def calculate_weighted_averages(
    df: pd.DataFrame, group_cols: list, metric_cols: list, weight_col: str
):
    """
    For certain aggregations, we need to calculate a weighted average,
    weighted by the number of trips.

    If we want peak/offpeak weighted calculations,
    we can take time-of-day (AM peak, PM peak) and
    get a peak speed calculation, after weighting by the number
    of trips present in each time-of-day bin.

    Ex: metric_cols = ['p20_mph', 'p50_mph', 'p80_mph']
    weight_cols = 'n_trips'

    """
    for c in metric_cols:
        df[c] = df[c] * df[weight_col]

    df2 = (
        df.groupby(group_cols)
        .agg({c: "sum" for c in metric_cols + [weight_col]})
        .reset_index()
    )

    for c in metric_cols:
        df2[c] = df2[c].divide(df2[weight_col]).round(2)

    return df2

In [ ]:
all_metrics_test2 = calculate_weighted_averages(
    df=all_day,
    group_cols=[
        "quarter",
        "Organization",
        "schedule_gtfs_dataset_key",
        "Route ID",
        "dir_0_1",
        "Direction",
    ],
    metric_cols=[
        "Average VP per Minute",
        "% VP within Scheduled Shape",
        "Average Scheduled Service (trip minutes)",
    ],
    weight_col="# Trips with VP",
)

In [ ]:
all_metrics_test2.loc[
    (all_metrics_test2.Organization == "San Diego Metropolitan Transit System")
    & (all_metrics_test2["Route ID"] == "1")
    & (all_metrics_test2.quarter == "2023Q2")
    & (all_metrics_test2.Direction == "Eastbound")
]